# RW API Import

This notebook deals with the import of RW API data into [API Highways](https://apihighways.org).

In [74]:
import requests
from IPython.display import HTML, display
import tabulate
import csv
import time
import collections

In [75]:
# Generating an initial list
all_datasets = requests.get("https://api.resourcewatch.org/v1/dataset?page[size]=1000&page[number]=1&env=production,preproduction&includes=metadata&application=rw,gfw,aqueduct,prep").json()['data']

summary_info = map(lambda dataset: [
    ', '.join(dataset['attributes']['application']) if len(dataset['attributes']['application']) >= 2 else dataset['attributes']['application'][0],
    # dataset['attributes']['application'],
    dataset['attributes']['name'],
    dataset['attributes']['provider'],
    dataset['attributes']['type'],
    dataset['attributes']['connectorUrl'],
    len(dataset['attributes']['metadata']),
    dataset['id'],
], all_datasets)

display(HTML(tabulate.tabulate(summary_info, tablefmt='html')))

In [76]:
all_datasets[0]

{'attributes': {'application': ['prep'],
  'attributesPath': None,
  'blockchain': {},
  'clonedHost': {},
  'connectorType': 'document',
  'connectorUrl': 'https://raw.githubusercontent.com/fgassert/PREP-washington-observed-data/master/observed_precip.csv',
  'dataPath': None,
  'env': 'production',
  'errorMessage': None,
  'geoInfo': False,
  'layerRelevantProps': [],
  'legend': {'country': [], 'date': [], 'nested': [], 'region': []},
  'mainDateField': None,
  'metadata': [{'attributes': {'application': 'prep',
     'citation': 'Vose, R. S. et al., 2014. Improved historical temperature and precipitation time series for US climate divisions. Journal Of Applied Meteorology and Climatology, 53(5), 1232-1251.',
     'createdAt': '2016-12-13T10:02:28.337Z',
     'dataset': '06c44f9a-aae7-401e-874c-de13b7764959',
     'description': 'These data were derived from the U.S. Climate Divisional Dataset, developed by the National Centers for Environmental Information (NCEI). NCEI provides lon

In [49]:
# After inspection and manually dropping some of the datasets of the list, we'll parse those with a single metadata object.

datasets = dict()

with open('./data/single_metadata.csv', 'r') as csvfile:
    reader = csv.reader(csvfile, delimiter=',', quotechar='"')
    for row in reader:
        dataset_id = row[0]
        dataset_url = f"https://api.resourcewatch.org/v1/dataset/{dataset_id}"
        metadata_url = f"https://api.resourcewatch.org/v1/dataset/{dataset_id}/metadata"
        dataset = requests.get(dataset_url).json()['data']
        # Sleep for a little bit
        dataset['metadata'] = (requests.get(metadata_url).json())['data'][0]
        datasets[dataset_id] = dataset
        
        time.sleep(1)
        
        # datasets[dataset_id] = dataset
datasets

{'018719a6-009b-4b04-970d-08b93c8192cb': {'attributes': {'application': ['rw'],
   'attributesPath': None,
   'blockchain': {},
   'clonedHost': {},
   'connectorType': 'document',
   'connectorUrl': 'http://wri-api-backups.s3.amazonaws.com/raw/1520975652559_WorldData-Withdrawal_eng.csv',
   'dataPath': '',
   'env': 'production',
   'errorMessage': '',
   'geoInfo': False,
   'layerRelevantProps': [],
   'legend': {'country': [], 'date': [], 'nested': [], 'region': []},
   'mainDateField': None,
   'name': 'Water withdrawals by sector',
   'overwrite': False,
   'protected': False,
   'provider': 'csv',
   'published': False,
   'slug': 'Water-withdrawals-by-sector',
   'status': 'saved',
   'subtitle': '',
   'tableName': 'index_018719a6009b4b04970d08b93c8192cb_1520975655098',
   'taskId': '/v1/doc-importer/task/bdebdda7-42ce-4fa2-8100-8906f2f295ae',
   'type': 'tabular',
   'updatedAt': '2018-03-13T21:14:26.740Z',
   'userId': '57d021e329309063404573a8',
   'verified': False,
   'wi

In [77]:
# 'info' has a free schema - let's see what fields are used
all_metadata_fields = list(map(lambda dset_key: 
                        (
                            # list(datasets[dset_key]['metadata']['data'][0]['attributes'].keys()),
                            list(datasets[dset_key]['metadata']['attributes']['info'].keys())
                        ),
                        datasets))

def flatten(l):
    for el in l:
        if isinstance(el, collections.Iterable) and not isinstance(el, (str, bytes)):
            yield from flatten(el)
        else:
            yield el

unique_metadata_fields = set(flatten(all_metadata_fields))
unique_metadata_fields

{'cautions',
 'citation',
 'dataDownload',
 'data_download_link',
 'data_download_original_link',
 'data_type',
 'date_of_content',
 'description',
 'endpoint',
 'frequency_of_updates',
 'function',
 'functions',
 'geographic_coverage',
 'language',
 'learn_more_link',
 'license',
 'license_link',
 'loca',
 'name',
 'nexgddp',
 'organization',
 'organization-long',
 'published_date',
 'rwId',
 'service',
 'short-description',
 'source',
 'sources',
 'spatial_resolution',
 'subtitle',
 'technical_title',
 'title',
 'wri_rw_id'}

In [99]:
from functools import reduce
def get_field(dataset, fields):
    try:
        result = reduce(lambda c, k: c.get(k, None), fields, dataset)
    except:
        result = None
    return result

def gen_main_url(apps, dataset):
    # print(dataset)
    app = apps[0]
    dataset_id = dataset['id']
    try:
        main_url = {
            'prep': f'https://www.prepdata.org/dataset/{dataset_id}',
            'gfw': f'https://production-api.globalforestwatch.org/v1/dataset/{dataset_id}',
            'rw': f'https://api.resourcewatch.org/v1/dataset/{dataset_id}',
            'aqueduct': f'http://www.wri.org/applications/maps/aqueduct-atlas/' 
        }[app]
    except:
        return ''
    
    return main_url

def get_fields(dataset):
    apps = dataset['attributes']['application']
    #print(apps)
    out = {
        "dset_id": dataset['id'],
        "dset_name": dataset['attributes']['name'],
        #"dset_desc": dataset['attributes']['description'],
        "dset_provider": dataset['attributes']['provider'],
        "dset_type": dataset['attributes']['type'],
        "dset_published": dataset['attributes']['published'],
        "dset_connector": dataset['attributes']['connectorType'],
        "dset_curl": dataset['attributes']['connectorUrl'],
        "dset_env": dataset['attributes']['env'],
        "dset_last_update": dataset['attributes']['updatedAt'],
        "dset_apps": ', '.join(dataset['attributes']['application']) if len(dataset['attributes']['application']) >= 2 else dataset['attributes']['application'][0],
        "metadata_source": get_field(dataset, ['metadata', 'attributes', 'source']),
        "metadata_desc": get_field(dataset, ['metadata', 'attributes', 'description']),
        "platform_url": gen_main_url(apps, dataset)
    }
    # applications = dataset['attributes']['application'] if len(dataset['attributes']['application']) >= 2 else dataset['attributes']['application']
    return out

final_res = [get_fields(datasets.get(dataset)) for dataset in datasets]
display(HTML(tabulate.tabulate(final_res, tablefmt='html')))

In [96]:
gen_main_url(['rw'], datasets['09b01386-7614-47fb-ac9f-c9cccf86bc9d'])

'https://api.resourcewatch.org/v1/dataset/{id}'